In [47]:
import os
import sys
import pyspark.pandas as ps

from pyspark.sql import SparkSession
from pyspark.sql.functions import col, expr
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import Normalizer
from pyspark.ml.feature import StandardScaler
from pyspark.ml.linalg import DenseVector, Vectors, VectorUDT
from pyspark.ml.feature import BucketedRandomProjectionLSH
from pyspark.ml.feature import PCA
from pyspark.sql import SparkSession
from pyspark.sql.functions import col
from pyspark.ml.feature import Normalizer
from pyspark.ml.linalg import Vectors
from pyspark.ml.feature import SQLTransformer
from pyspark.sql.functions import udf


#Initialize a spark session
spark = SparkSession.builder \
    .appName("recommenderTest") \
    .config("spark.some.config.option", "some-value") \
    .config("spark.executor.memory", "4g") \
    .config("spark.driver.memory", "4g") \
    .config("spark.sql.shuffle.partitions", "100") \
    .config("spark.sql.pivotMaxValues", "20000") \
    .config("spark.master", "local[8]") \
    .getOrCreate()
# --- Data Pre-Processing ---

# Load the data into an DF (userId,movieId,rating,timestamp)

# File format: userId,movieId,rating,timestamp
df = spark.read.csv("data/ratings_small.csv", header=True, inferSchema=True)
df = df.drop("timestamp") # drop timestamp column

# Group by userId and pivot the movieId column
df = df.groupBy("userId").pivot("movieId").agg({"rating": "first"}).fillna(0)
df.show(100)

# Cast all columns to float
df = df.select([col(col_name).cast("float") for col_name in df.columns])

# UDF to create DenseVector from ratings
def create_dense_vector(ratings_list):
    return DenseVector(ratings_list)

vector_udf = udf(create_dense_vector, VectorUDT())

# Create a new DataFrame with userId and ratings as a DenseVector
rating_columns = [col_name for col_name in df.columns if col_name != "userId"]
df_vector = df.select("userId", vector_udf(*rating_columns).alias("ratings"))

df_vector.show(10)



# SPLIT THIS CODE IN MULTIPLE PART TO MAKE COMPUTING FASTER

# first_two_rows = df.take(2)
# row1 = Vectors.dense(first_two_rows[0][1:])
# row2 = Vectors.dense(first_two_rows[1][1:])
# dot_product = row1.dot(row2)
# magnitude_row1 = row1.norm(2)
# magnitude_row2 = row2.norm(2)
# cosine_similarity = dot_product / (magnitude_row1 * magnitude_row2)
# print("Cosine similarity: ", cosine_similarity)
# (df_size_rows, df_size_cols) = df.toPandas().shape
# print("DataFrame size: ", df_size_rows, "rows x", df_size_cols, "columns")






23/03/22 14:12:47 WARN DAGScheduler: Broadcasting large task binary with size 1929.1 KiB


23/03/22 14:12:51 WARN DAGScheduler: Broadcasting large task binary with size 7.1 MiB


+------+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+

NameError: name 'array' is not defined